In [1]:
!pip install folium
%matplotlib
%matplotlib inline
import folium
import requests
import os
import pandas

arrest_table = pandas.read_csv("http://www.hcbravo.org/IntroDataSci/misc/BPD_Arrests.csv")

arrest_table["race_new"] = arrest_table["sex"]
arrest_table["sex_new"] = arrest_table["race"]
arrest_table["race"] = arrest_table["race_new"]
arrest_table["sex"] = arrest_table["sex_new"]
arrest_table = arrest_table.drop('race_new', 1)
arrest_table = arrest_table.drop('sex_new', 1)

arrest_table = arrest_table[pandas.notnull(arrest_table["Location 1"])]

arrest_table["lat"], arrest_table["long"] = arrest_table["Location 1"].str.split(",").str
arrest_table["lat"] = arrest_table["lat"].str.replace("(", "").astype(float)
arrest_table["long"] = arrest_table["long"].str.replace(")", "").astype(float)



Using matplotlib backend: MacOSX


In [2]:
import folium
import pandas as pd
m = folium.Map([39.281403,-76.648364], zoom_start=4)


gun_df = pd.DataFrame()
for index,row in arrest_table.iterrows():
    #if substring in someString:
    if("gun".upper() in str(arrest_table.loc[index,'chargeDescription']).upper() or "firearm".upper() in str(arrest_table.loc[index,'chargeDescription']).upper()):
        gun_df = gun_df.append(row)
        
        
#gun df is a df containing all rows from original df that have "gun" or "firearm" (made it case insenstive)
#gun_df

In [3]:
with open('baltimore.geojson', 'r') as myfile:
    data=myfile.read().replace('\n', '')

# definition of the boundaries in the map
district_geo = r'baltimore.geojson'
 
# calculating total number of incidents per district
crimedata = pd.DataFrame(gun_df['neighborhood'].value_counts().astype(float))
crimedata.to_json('crimeagg.json')
crimedata = crimedata.reset_index()
crimedata.columns = ['neighborhood', 'Number']
for index,row in crimedata.iterrows():
    if crimedata.loc[index,'neighborhood'] not in data:
        #print(crimedata.loc[index,'neighborhood'])
        crimedata.drop(index, inplace=True)



#creation of the choropleth
map1 = folium.Map(location=(39.281403,-76.648364), zoom_start=11)
map1.choropleth(geo_path = district_geo, 
              data_out = 'crimeagg.json', 
              data = crimedata,
              columns = ['neighborhood', 'Number'],
              key_on = 'feature.properties.name',
              fill_color = 'YlOrRd', 
#               fill_opacity = 0.7, 
#               line_opacity = 0.2,
              legend_name = 'Number of gun-related incidents per neighborhood')
              
map1


In [4]:
# calculating total number of general arrests per neighborhood
crimedata = pd.DataFrame(arrest_table['neighborhood'].value_counts().astype(float))
crimedata.to_json('crimeagg.json')
crimedata = crimedata.reset_index()
crimedata.columns = ['neighborhood', 'Number']
for index,row in crimedata.iterrows():
    if crimedata.loc[index,'neighborhood'] not in data:
        crimedata.drop(index, inplace=True)




 
#creation of the choropleth
map2 = folium.Map(location=(39.281403,-76.648364), zoom_start=11)
map2.choropleth(geo_path = district_geo, 
              data_out = 'crimeagg.json', 
              data = crimedata,
              columns = ['neighborhood', 'Number'],
              key_on = 'feature.properties.name',
              fill_color = 'YlOrRd', 
#               fill_opacity = 0.7, 
#               line_opacity = 0.2,
              threshold_scale= [0, 650, 1300, 1950, 2600, 3260],
              legend_name = 'Number of arrests per neighborhood')
              
map2